In [ ]:
# add zebrafish exp in heart to file
# add TF info?

In [2]:
library(dplyr)
library(ggplot2)

In [5]:
df1 = read.delim('20240213_candidate_CHD_genes.csv', sep = ',')
colnames(df1)[5] = 'CHD_DEG'
dim(df1)
df1[1:2,]

[1] 640   6

Gene    singlecell_score bulk_score CHD_gene CHD_DEG pLI
1 PITPNC1 0.9957024        0.8256721  0        1       1  
2 EEF1A1  0.9904411        0.9614385  0        1       1

In [17]:
pb = read.delim('~/Atlas/TOME/saturn/zebrafish_pseudobulk_expression.csv', sep = ',')
dim(pb)
pb[c('tbx5a', 'tbx3a'),]

[1] 30032    32

Neural.crest Optic     Eye.primordium Neuroectoderm Notoplate Neuron  
tbx5a 9.483519      5.143463 12.13516       15.167559     11.200492 10.76083
tbx3a 3.796658     27.237830 35.22303        3.735377      2.178432 23.71243
      Rohon.beard.neuron Forebrain.midbrain Hindbrain Non.neural.ectoderm ⋯
tbx5a   9.725261         8.294249           8.278383  13.218731           ⋯
tbx3a 101.707385         7.156646           3.394312   4.214915           ⋯
      Pronephric.mesenchyme Blood    Macrophage Endothelial
tbx5a 18.68849              4.799272 2.293080   6.407633   
tbx3a 14.16570              2.550003 2.251603   9.259315   
      Dorsal.Spemann.organizer Notochord Hatching.gland
tbx5a 11.673503                15.63386   3.414127     
tbx3a  5.622631                77.89812  15.187182     
      Involuting.marginal.zone Endoderm Blastula 
tbx5a 12.966001                13.44347 11.209663
tbx3a  4.810993                39.15601  6.258127

In [12]:
ginfo = read.delim('/data/CoCoCoNet/geneInfo/human_info.csv', sep = ',')
zinfo = read.delim('/data/CoCoCoNet/geneInfo/zebrafish_info.csv', sep = ',')

In [20]:
# human orthologs
om = read.delim('/data/suresh/spetree/scoresNM/human_zebrafish_odb_ensembl_agg_pairwise_LCA.csv', sep = ',')
om[,1] <- ginfo$GeneSymbol[match(om[,1], ginfo$NetworkIDs)]
om[,2] <- zinfo$GeneSymbol[match(om[,2], zinfo$NetworkIDs)]
om <- om[!is.na(om[,1]) & !is.na(om[,2]) & !is.na(om$sc),]

om$zfish_exp = pb$Heart[match(om[,2], rownames(pb))]
om[1:2,]

sp1_gene sp2_gene fc        sc        zfish_exp
1 INTS1    ints1    0.8014000 0.8625990 51.82547 
2 ELMO1    elmo2    0.6290222 0.7919592  2.40013

In [28]:
# for each gene, pick ortholog with exp > 5 and highest sc score
df1$zebrafish_ortholog = NA
df1$zebrafish_exp = NA
pb = txtProgressBar(min = 0, max = dim(df1)[1], initial = 0)

for(ii in 1:dim(df1)[1]){
    g1 = df1$Gene[ii]
    temp = om[om[,1]==g1,]
    
    if(dim(temp)[1]>0 & sum(!is.na(temp$zfish_exp))>0){
        temp<- temp[!is.na(temp$zfish_exp),]
        
        if(dim(temp)[1]>0){
            temp <- temp[which.max(temp$sc),]
            df1$zebrafish_ortholog[ii] = temp$sp2_gene[1]
            df1$zebrafish_exp[ii] = temp$zfish_exp[1]
        }
    }
    setTxtProgressBar(pb, ii)    
}
sum(!is.na(df1$zebrafish_exp))
head(df1)

[1] 554

Gene    singlecell_score bulk_score CHD_gene CHD_DEG pLI zebrafish_ortholog
1 PITPNC1 0.9957024        0.8256721  0        1       1   NA                
2 EEF1A1  0.9904411        0.9614385  0        1       1   eef1a1l1          
3 MAOA    0.9902877        0.8632752  0        1       1   si:ch211-127i16.2 
4 MAP4    0.9902652        0.9622695  0        1       1   NA                
5 GNAQ    0.9889745        0.9288898  0        1       1   gna11a            
6 KANK2   0.9863484        0.9263029  0        1       1   NA                
  zebrafish_exp
1          NA  
2 15658.18510  
3     4.44167  
4          NA  
5    54.07912  
6          NA

In [30]:
# add human TF info
tf = read.delim('~/septation/Homo_sapiens_TF.txt', sep = '\t')
tf[1,]

Species      Symbol Ensembl         Family  Protein            Entrez_ID
1 Homo_sapiens ATF1   ENSG00000123268 TF_bZIP ENSP00000262053.3; 466

In [31]:
# add tf or not
ids = match(df1$Gene, tf$Symbol)
df1$TF = 0
df1$TF[which(!is.na(ids))] = 1

In [36]:
df2 = df1 %>% arrange(CHD_gene, desc(CHD_DEG), desc(pLI), desc(TF), desc(zebrafish_exp))
head(df2)

Gene   singlecell_score bulk_score CHD_gene CHD_DEG pLI zebrafish_ortholog
1 TCF7L2 0.9509773        0.9244695  0        1       1   tcf7l1a           
2 ZMIZ1  0.9520540        0.9504114  0        1       1   zmiz2             
3 FOXP1  0.9567419        0.9051843  0        1       1   foxp1a            
4 DACH1  0.9515026        0.8637750  0        1       1   dachd             
5 GLI2   0.9566796        0.9654852  0        1       1   gli3              
6 EEF1A1 0.9904411        0.9614385  0        1       1   eef1a1l1          
  zebrafish_exp TF
1   103.095166  1 
2    56.494366  1 
3    54.519546  1 
4    41.662289  1 
5     5.729818  1 
6 15658.185101  0

In [37]:
# save
write.table(df2, file = '20240614_candidate_CHD_genes.csv', sep = ',', row.names = F, col.names = T,
           quote = F)